# Noyau et image d'une application linéaire

Marc Lorenzi

3 février 2020

In [ ]:
import random

## 0. Introduction

### 0.1 Objectifs, notations

Soit $f\in\mathcal L(E, F)$ une application linéaire entre deux $\mathbb R$-espaces vectoriels de dimension finie. Ce notebook se propose d'utiliser les méthodes vue en cours pour le calcul pratique de certaines quantités associées à $f$ : son rang, son noyau et son image. Les fonctions que nous allons développer permettront évidemment de déterminer aussi l'espace engendrée par une famille de vecteurs le rang de cette famille.

L'idée n'est pas d'avoir une boîte noire, d'excellentes bibliothèques existent déjà pour calculer ces quantités. Bien au contraire, le but est de comprendre comment on calcule un rang, un espace engendré, un noyau, etc. On laisse à l'utilisateur l'initiative des opérations à effectuer. L'automatisation viendra petit à petit ... jusqu'à l'écriture de deux fonctions `ker` et `im` qui feront toutes seules le calcul d'une base du noyau et de l'image de $f$.

Nous verrons ensuite comment ce que nous avons fait permet de travailler sur les sous-espaces vectoriels de $E$ : bases, équations cartésiennes, sommes, intersections, supplémentarité, etc.

__Remarque__ : Comme beaucoup de calculs pratiques font intervenir des matrices d'entiers, nous ferons en sorte que nos opérations préservent cette propriété. Tous nos calculs seront donc exacts et jamais approchés.

### 0.2 Matrices d'exemples

Nous allons bien évidemment travailler sur des matrices, que nous représenterons en Python comme des listes de listes. Voici une fonction renvoyant une matrice que nous prendrons fréquemment comme exemple.

In [ ]:
def exemple(p=3, q=3):
    n = p * q
    A = [q * [0] for i in range(p)]
    for k in range(n):
        A[k % p][k // p] = k + 1
    return A

In [ ]:
exemple(5, 4)

Nous aurons souvent besoin du nombre de lignes et du nombre de colonnes d'une matrice.

In [ ]:
def nblig(A): return len(A)
def nbcol(A): 
    if A == []: raise Exception('Nombre de colonnes indetermine')
    return len(A[0])

In [ ]:
A = exemple(7, 8)
nblig(A), nbcol(A)

Écrivons également une fonction qui permet d'avoir un affichage des matrices plus agréable. On évalue et on stocke pour chaque colonne de la matrice la longueur maximale de la représentation de ses coefficients sous forme de chaîne de caractères. Puis on affiche la matrice ligne par ligne en utilisant les longueurs maximales pré-calculées. La matrice est alors parfaitement tabulée.

In [ ]:
def prnt(A):
    if A == []: print('_')
    else:
        p, q = nblig(A), nbcol(A)
        ws = q * [0]
        for j in range(q):
            for i in range(p):
                w = len('%s' % (A[i][j]))
                if w > ws[j]: ws[j] = w
        for i in range(p):
            s = ''
            for j in range(q):
                s1 = '%d' % A[i][j]
                sp = ws[j] - len(s1) + 1
                s1 = (sp * ' ') + s1
                s = s + s1
            print(s)

In [ ]:
prnt(exemple(12, 25))

Nous utiliserons aussi parfois des matrices aléatoires. La fonction `randmat` renvoie une matrice "aléatoire" de taille $p\times q$ dont les coefficients sont des entiers de l'intervalle $[-r,r]$.

In [ ]:
def randmat(p, q, r=10):
    A = [q * [0] for i in range(p)]
    for i in range(p):
        for j in range(q):
            A[i][j] = random.randint(-r, r)
    return A

In [ ]:
A = randmat(10, 15, r=10000)
prnt(A)

## 1. Rang, espace engendré

### 1.1 Introduction

On ne change pas l'espace engendré par les colonnes de la matrice $A$ (et donc pas non plus son rang) en effectuant les opérations suivantes :

- Échanger deux colonnes.
- Multiplier une colonne par un réel non nul.
- Ajouter à une colonne un multiple d'un autre colonne.

Nous allons tout d'abord définir ces opérations au moyen de quelques fonctions qui se passent de commentaires.

### 1.2 Échange de deux colonnes

La fonction `echanger` échange les colonnes $j_1$ et $j_2$ de la matrice $A$.

$$C_{j_1}\longleftrightarrow C_{j_2}$$

In [ ]:
def echanger(A, j1, j2, dbg=True):
    if dbg: print('C%s <-> C%s' % (j1, j2))
    for i in range(nblig(A)):
        A[i][j1], A[i][j2] = A[i][j2], A[i][j1]

In [ ]:
A = exemple(5, 8)
echanger(A, 3, 6)
prnt(A)

### 1.3 Produit d'une colonne par un scalaire 

La fonction `mult` multiplie la colonne $j$ de la matrice $A$ par le scalaire $t$.

$$C_j \longleftarrow t C_j$$

In [ ]:
def mult(A, j, t, dbg=True):
    if dbg: print('C%s <- (%s)C%s' % (j, t, j))
    for i in range(nblig(A)):
        A[i][j] = t * A[i][j]

In [ ]:
A = exemple(5, 10)
mult(A, 4, -5)
prnt(A)

Histoire de pouvoir aussi diviser une colonne par un facteurs commun de ses éléments, définissons une fonction `div`.

In [ ]:
def div(A, j, t, dbg=True):
    if dbg: print('C%s <- (1/%s)C%s' % (j, t, j))
    for i in range(nblig(A)):
        A[i][j] = A[i][j] // t

In [ ]:
A = [[5, 10], [15, 20]]
prnt(A)
div(A, 0, 5)
div(A, 1, 10)
prnt(A)

### 1.4 Ajout à une colonne d'un multiple d'une autre colonne

La fonction `add` ajoute à la colonne $j_1$ de la matrice $A$ $t$ fois la colonne $j_2$.

$$C_{j_1} \longleftarrow C_{j_1} + t C_{j_2}$$

In [ ]:
def add(A, j1, t, j2, dbg=True):
    if dbg: print('C%s <- C%s + (%s)C%s' % (j1, j1, t, j2))
    for i in range(nblig(A)):
        A[i][j1] = A[i][j1] + t * A[i][j2]

In [ ]:
A = exemple(5, 10)
add(A, 2, -11, 0)
add(A, 7, -36, 0)
prnt(A)

### 1.5 Pivot

Première étape de l'automatisation, la fonction `pivoter` combine certaines des opérations déjà décrites. Soit $A$ une matrice $p\times q$. La fonction `pivoter` prend en paramètres un indice de ligne $\ell$ et un indice de colonne $k$ tels que $t=A_{\ell k}\ne 0$. Le but de `pivoter` est d'annuler les coefficients $A_{\ell(k+1)},A_{\ell(k+2)},\ldots,A_{\ell q}$. 

Pour $j=k+1,\ldots,q-1$, on effectue l'opération 

$$C_j\longleftarrow \frac t \delta C_j - \frac u \delta C_k$$

où $u=A_{\ell j}$ et $\delta =pgcd(t,u)$. La fonction `pivoter` effectue au total $2(q-k)$ opérations "élémentaires" sur les colonnes de $A$. Elle remplit bien son rôle puisque

$$\frac t \delta A_{\ell j} - \frac u \delta A_{\ell k}=\frac t \delta u - \frac u \delta t=0$$

__Remarque__ : On pourrait automatiser `pivoter` afin que la fonction trouve elle-même les indices $\ell$ et $k$. Nous le ferons plus loin mais pour l'instant il est du devoir de l'utilisateur d'observer la matrice $A$ et de choisir les valeurs de $\ell$ et de $k$ qui lui semblent pertinentes !

In [ ]:
def gcd(a, b):
    while b != 0:
        a, b = b, a % b
    return a

In [ ]:
def pivoter(A, l, k, dbg=True):
    t = A[l][k]
    for j in range(k + 1, nbcol(A)):
        u = A[l][j]
        d = gcd(t, u)
        if dbg: print('C%s <- (%s)C%s + (%s)C%s' % (j, t // d, j, -u // d, k))
        for i in range(0, nblig(A)):
            A[i][j] = (t // d) * A[i][j] - (u // d) * A[i][k]

In [ ]:
A = exemple(5, 6)
pivoter(A, 0, 0)
prnt(A)

Maintenant que les fonctions de base sont mises en place, regardons ce que l'on peut faire avec.

## 2. Quelques exemples

### 2.1 Notre exemple préféré

Prenons tout d'abord notre matrice favorite.

In [ ]:
A = exemple(6, 9)
prnt(A)

On pivote en 0,0.

In [ ]:
pivoter(A, 0, 0)
prnt(A)

Puis en 1, 1.

In [ ]:
pivoter(A, 1, 1)
prnt(A)

Effectuons une dernière opération.

In [ ]:
div(A, 1, A[1][1])
prnt(A)

Cette matrice a même rang que $A$ et ses colonnes engendrent le même espace que les colonnes de $A$. Ainsi, $rg A=2$ et l'image d'une application linéaire associée à $A$ a pour base les deux premières colonnes de $A$.  

### 2.2 Rang d'une famille de vecteurs

On se place dans $E=\mathbb R^5$. Soient 
- $x_1=(1,2,-4,3,1)$
- $x_2=(2,5,-3,4,8)$ 
- $x_3=(6,17,-7,10,22)$
- $x_4=(1,3,-3,2,0)$
Quel est le rang de la famille $(x_1,x_2, x_3,x_4)$ ? 

Tout d'abord, voici une fonction bien utile qui renvoie la transposée d'une matrice. Cela évite de faire de la gymnastique pour entrer les données en lignes alors qu'on nous les donne en colonnes.

In [ ]:
def transp(A):
    if A == []: return []
    p, q = nblig(A), nbcol(A)
    B = [p * [0] for i in range(q)]
    for i in range(q):
        for j in range(p):
            B[i][j] = A[j][i]
    return B

In [ ]:
A = transp([[1, 2, -4, 3, 1], [2, 5, -3, 4, 8], [6, 17, -7, 10, 22], [1, 3, -3, 2, 0]])
prnt(A)

Et maintenant, pivotons.

In [ ]:
pivoter(A, 0, 0)
prnt(A)

In [ ]:
pivoter(A, 1, 1)
prnt(A)

In [ ]:
pivoter(A, 2, 2)
prnt(A)

Encore une petite simplification ...

In [ ]:
div(A, 2, -2)
prnt(A)

Le rang de la famille $(x_1,\ldots,x_4)$ est donc 3.

### 2.3 Matrices aléatoires

Ne prenez surtout pas exemple sur la fonction qui vient ... La fonction `kamikaze` appelle `pivot` successivement sur les indices $(0, 0), (1, 1),\ldots,(m,m)$ où $m=\min(p,q)$, en priant pour ne jamais tomber sur un pivot nul. Cela a de bonnes chances de fonctionner sur une matrice aléatoire, et quasiment aucune chance de fonctionner sur des matrices particulières, surtout sur les matrices qui apparaissent dans les exercices classiques :-).

In [ ]:
def kamikaze(A, dbg=True):
    m = min(nblig(A), nbcol(A))
    for k in range(m):
        pivoter(A, k, k, dbg)

In [ ]:
A = randmat(4, 6)
kamikaze(A, dbg=True)
prnt(A)

Depuis quelque temps nous avons remarqué que, souvent, des entiers sont en facteurs dans les colonnes. Écrivons une fonction qui divise une colonne d'une matrice par le pgcd des coefficients de cette colonne.

In [ ]:
def gcdcol(A, j):
    d = 0
    for i in range(nblig(A)):
        d = gcd(d, A[i][j])
    return d

In [ ]:
def normaliser_colonne(A, j, dbg):
    d = gcdcol(A, j)
    if d != 0:
        div(A, j, d, dbg)

Voici notre nouvelle fonction `kamikaze` qui simplifie, après chaque appel à pivot, la colonne dans laquelle se trouve le pivot.

In [ ]:
def kamikaze2(A, dbg=True):
    for k in range(min(nblig(A), nbcol(A))):
        pivoter(A, k, k, dbg)
        normaliser_colonne(A, k, dbg)

Testons.

In [ ]:
A = randmat(4, 6)
kamikaze2(A, dbg=True)
prnt(A)

Une matrice $13\times 13$ pour terminer ? Des matrices de taille $100\times 100$ sont parfaitement envisageables, mais inutile alors d'espérer les afficher joliment ... 

In [ ]:
A = randmat(13, 13)
prnt(A)

En zéro seconde, `kamikaze2` renvoie le résultat.

In [ ]:
kamikaze2(A, dbg=False)
prnt(A)

## 3. Noyau et image

### 3.1 Introduction

Soit $A\in\mathcal M_{pq}(\mathbb K)$. La matrice $A$ est la matrice dans les bases canoniques de $\mathbb K^q$ et $\mathbb K^p$ d'une application linéaire $f$. Que valent le noyau et l'image de $f$ ?

Pour l'image de $f$ c'est facile. En effet les opérations "élémentaires" sur les colonnes de $A$ ne changent pas l'espace engendré par les colonnes. Bref, nous avons déjà écrit une fonction qui calcule une base $Im f$. On pivote et on récupère les colonnes non nulles de la matrice finale.

Pour le noyau de $f$, il va nous falloir être un peu plus soigneux. 

Appelons $\mathcal B=(e_1,\ldots,e_q)$ la base canonique de $\mathbb K^q$. Soit $\mathcal B'$ la base canonique de $\mathbb K^p$. 

À chaque opération sur les colonnes de $A$ nous allons enregistrer quelle opération a été effectuée. Où enregistrer cela ? Dans une matrice $B\in GL_q(\mathbb K)$ qui est la matrice de passage d'une base de $\mathbb K^q$ à la base $\mathcal B$. La matrice $B$ est initialement la matrice identité $I_q=P_{\mathcal B}^{\mathcal B}$. Lors d'une opération élémentaire sur les colonnes de $A$ on effectue la même opération sur la matrice $B$. Et alors ? La matrice $A$ est la matrice de $f$ dans les bases $\mathcal B$ et $\mathcal B'$ : la $j$ème colonne de $A$ contient donc le vecteur $f(e_j)$ (ou plutôt ses coordonnées dans la base $\mathcal B'$).

Prenons un exemple concret : effectuons l'opération $C_2 \longleftarrow C_2 + 3C_1$. La colonne 2 de $A$ contient alors $f(e_2+3e_1)$. Si l'on effectue la même opération sur la matrice $B$, celle-ci devient la matrice de passage de $\mathcal B$ à une nouvelle base qui a les mêmes vecteurs que $\mathcal B$, sauf le second qui vaut $e_2+3e_1$. Nous avons ainsi "stocké" $e_2+3e_1$ dans la matrice $B$.

De façon générale, $B=P_{\mathcal B}^{\mathcal B_1}$ où $\mathcal B_1$ est telle que $A=mat_{\mathcal B_1\mathcal B'}f$.

Au travail !

### 3.2 Réécriture des opérations élémentaires

Ces fonctions sont identiques à celles qui ont déjà été écrites, mis à part le fait qu'elle prennent un paramètre $B$ supplémentaire qui est la matrice de passage décrite au paragraphe précédent. Chaque opération sur $A$ est répercutée sur $B$.

In [ ]:
def echanger2(A, j1, j2, B):
    for i in range(nblig(A)):
        A[i][j1], A[i][j2] = A[i][j2], A[i][j1]
    for i in range(nblig(B)):
        B[i][j1], B[i][j2] = B[i][j2], B[i][j1]

In [ ]:
def mult2(A, j, t, B):
    for i in range(nblig(A)):
        A[i][j] = t * A[i][j]
    for i in range(nblig(B)):
        B[i][j] = t * B[i][j]

In [ ]:
def div2(A, j, t, B):
    for i in range(nblig(A)):
        A[i][j] = A[i][j] // t
    for i in range(nblig(B)):
        B[i][j] = B[i][j] // t

In [ ]:
def add2(A, j1, t, j2, B):
    for i in range(nblig(A)):
        A[i][j1] = A[i][j1] + t * A[i][j2]
    for i in range(nblig(B)):
        B[i][j1] = B[i][j1] + t * B[i][j2]

In [ ]:
def pivoter2(A, l, k, B):
    t = A[l][k]
    for j in range(k + 1, nbcol(A)):
        u = A[l][j]
        d = gcd(t, u)
        for i in range(0, nblig(A)):
            A[i][j] = (t // d) * A[i][j] - (u // d) * A[i][k]
        for i in range(0, nblig(B)):
            B[i][j] = (t // d) * B[i][j] - (u // d) * B[i][k]

La fonction `eye` renvoie la matrice identité d'ordre $n$, valeur initiale pour la matrice $B$.

In [ ]:
def eye(n):
    A = [n * [0] for i in range(n)]
    for i in range(n):
        A[i][i] = 1
    return A

Testons sur un exemple.

In [ ]:
A = exemple(5, 6)
B = eye(6)
prnt(A)
print()
prnt(B)

In [ ]:
pivoter2(A, 0, 0, B)
prnt(A)
print()
prnt(B)

In [ ]:
pivoter2(A, 1, 1, B)
prnt(A)
print()
prnt(B)

Bilan :

- Le rang de $A$ est 2. 
- Une base de $Im f$ est la famille des deux premières colonnes de $A$ (les colonnes non nulles).
- Une base de $\ker f$ est la famille des 4 dernières colonnes de $B$, celles qui correspondent aux colonnes nulles de $A$.



### 3.3 Automatisons le tout

Tout le problème, à chaque étape, est la recherche du pivot. Quelles valeurs prendre pour $k$ et $\ell$, passés en paramètres à `pivoter` ? À la $k$ième itération, le couple $(k,k)$ paraît judicieux. Mais il ne l'est pas toujours car le coefficient correspondant dans la matrice $A$ est peut-être nul. Sans justification dans ce notebook, l'idée est de choisir un couple $(\ell, k')$ où 

$$\ell=\min\{i\ge k, \exists j \ge k, A_{i j}\ne 0\}$$

$$k'=\min\{j\ge k, A_{\ell j}\ne 0\}$$

Ce couple d'indices se trouve à l'aide de deux boucles imbriquées. On parcourt les lignes $k,k+1,k+2,\ldots$ à partir de la colonne $k$ et on s'arrête dès qu'on trouve un coefficient non nul. On renvoie alors les indices de ligne et de colonne de ce coefficient. On cherche donc une ligne d'indice minimal à partir de la ligne $k$ et, pour cette ligne, un indice de colonne minimal, qui fournissent un coefficient non nul de la matrice.

Si un tel coefficient n'existe pas c'est qu'il n'y a plus aucune opération à faire sur la matrice $A$ parce que tous les coefficients observés sont nuls.

La fonction `chercher_pivot` cherche un tel couple $(\ell, k)$ d'indices. Elle renvoie $(\ell,k,True)$ si elle en trouve un, et $(-1,-1,False)$ sinon.

In [ ]:
def chercher_pivot(A, k):
    for i in range(k, nblig(A)):
        for j in range(k, nbcol(A)):
            if A[i][j] != 0: return (i, j, True)
    return (-1, -1, False)    

La fonction `imker` automatise tout ce que nous venons de raconter. Elle prend une matrice $A$ en paramètre et renvoie un couple $(A, B)$ où $A$ est la matrice "trigonalisée" et $B$ est une matrice de passage.

Petits détails :
- On opère sur une __copie__ de $A$ pour ne pas modifier la matrice initiale. 
- On divise en fin de fonction les colonnes d e$A* et $B$ par les pgcd de leurs coefficients pour avoir un résultat aussi simple que possible.

In [ ]:
def imker(A):
    A = [A[i].copy() for i in range(nblig(A))]
    B = eye(nbcol(A))
    k = 0
    while True:
        i, j, b = chercher_pivot(A, k)
        if not b: break
        if j != k: echanger2(A, j, k, B)
        pivoter2(A, i, k, B)
        k = k + 1
    for j in range(nbcol(A)): normaliser_colonne(A, j, dbg=False)
    for j in range(nbcol(B)): normaliser_colonne(B, j, dbg=False)
    return (A, B)

Testons.

In [ ]:
A = exemple(6, 10)
prnt(A)

In [ ]:
A1, B = imker(A)
prnt(A1)
print()
prnt(B)

### 3.4 Noyau, image

Tout a été dit : on appelle `imker`, qui renvoie deux matrices $A_1$ et $B$. Pour obtenir une base de $Im f$ on récupère les colonnes non nulles de $A_1$. Pour obtenir une base de $\ker f$, récupère les colonnes de $B$ qui correspondent aux colonnes nulles de $A_1$. Pourquoi cela fonctionne-t-il ?

Les opérations effectuées sur $B$ ne changent pas son rang. Or, $B=I$ au début de notre algorithme. La matrice renvoyée est donc inversible. De plus, par le théorème du rang, le nombre de colonnes nulles de $A_1$ est égal à $\dim\ker f$. En récupérant les colonnes correspondantes de $B$ on obtient donc une famille libre de $\ker f$ dont le cardinal est justement la dimension du noyau de $f$, c'est à dire une base.

In [ ]:
def noyau(A):
    A, B = imker(A)
    return transp([col(B, k) for k in col_nulles(A)])

In [ ]:
def image(A):
    A, B = imker(A)
    return transp([col(A, k) for k in range(nbcol(A)) if not (est_col_nulle(A, k))])

La fonction `col` renvoie la __liste__ des coefficients de la $j$ème colonne de $A$.

In [ ]:
def col(A, j):
    return [A[i][j] for i in range(nblig(A))]

La fonction `est_col_nulle` teste si la $j$ème colonne de $A$ ne contient que des zéros.

In [ ]:
def est_col_nulle(A, j):
    for i in range(nblig(A)):
        if A[i][j] != 0: return False
    return True

La fonction `col_nulles` renvoie la liste des numéros des colonnes nulles de $A$.

In [ ]:
def col_nulles(A):
    return [j for j in range(nbcol(A)) if est_col_nulle(A, j)]

Testons sur notre exemple habituel.

In [ ]:
A = exemple(6, 10)
prnt(noyau(A))
print()
prnt(image(A))

### 3.4 Vérifications

Voici une fonction calculant le produit de deux matrices $A$ et $B$.

In [ ]:
def prodmat(A, B):
    p, q = nblig(A), nbcol(A)
    q1, r= nblig(B), nbcol(B)
    if q1 != q: raise Exception('Matrices incompatibles')
    C = [q * [0] for i in range(p)]
    for i in range(p):
        for j in range(r):
            for k in range(q):
                C[i][j] += A[i][k] * B[k][j]
    return C

In [ ]:
A = exemple(8, 12)
prnt(A)

In [ ]:
B = noyau(A)
prnt(B)

Le produit $A B$ devrait être nul puisque (matriciellement) les colonnes de $B$ sont dans le noyau de $A$

In [ ]:
prnt(prodmat(A, B))

CQFD :-).

## 4. Équations cartésiennes

### 4.1 Bases et équations cartésiennes

Soit $F$ un sous-espace vectoriel de $\mathbb R^q$ de dimension $r$. Il existe essentiellement deux façons de se donner $F$.

- Par une base.
- Par un ensemble d'équations cartésiennes.

Deux questions se posent :

- Étant donnée une base de $F$, comment obtenir un ensemble minimal d'équations cartésiennes (la théorie nous annonce $q-r$ équations) ?
- Étant donné un ensemble minimal d'équations cartésiennes de $F$, comment en obtenir une base ?

__Remarque__ : Nous allons bientôt être frappés de plein fouet par le problème des __matrices vides__. Imaginons que $F=\{0\}$. Une base de $F$ est la famille vide, représentée par la matrice $[]$ qui a zéro colonne. Oui, mais combien de lignes a-t-elle ? On ne sait pas. Et pourtant, cette information est vitale, puisqu'elle nous donne la dimension de l'espace $E$ tout entier. Même problème avec les familles d'équations cartésiennes : L'espace tout entier est représenté par zéro équation, donc par une matrice de zéro ligne. Et nous ne savons plus quelle est sa dimension. Nous devrons donc, lors de l'écriture de nos fonctions, prévoir ce cas troublant.

### 4.2 Bases vers équations

La théorie nous dit que $F$, sev de dimension $r$ d'un espace $E$ de dimension $q$, est l'intersection de $q-r$ hyperplans $H_1,\ldots,H_{q-r}$. Comment obtenir des équations de tels hyperplans ? Soit $\mathcal F =(x_1,\ldots,x_{r})$ une base de $F$. Soient $\varphi_1,\ldots,\varphi_{q-r}$ $q-r$ formes linéaires non nulles dont les hyperplans cherchés sont les noyaux. Soit $f=(\varphi_1,\ldots,\varphi_{q-r})$. L'appplication $f$ est linéaire de $E$ vers $\mathbb R^{q-r}$ et son noyau est précisément $F$. Notons $A$ la matrice de $f$ dans une base  de $E$ et la base canonique de $\mathbb R^{q-r}$. Notons $B$ la matrice de $\mathcal F$ dans la base de $E$ susnommée. On a alors $AB=0$, ou encore

$$B^TA^T=0$$

où le $T$ désigne la transposition. Ainsi, les colonnes de $A^T$ sont les matrices dans la base de $E$ de vecteurs du noyau de $B^T$. Soit $g\in\mathcal L(\mathbb R^{q-r}, E)$ dont la matrice dans les bases (toujours les mêmes) de $E$ et $\mathbb R^{q-r}$ est $B^T$. Alors $A^T$ est la matrice d'une base du noyau de $g$.

Or, le théorème du rang nous dit que $\dim\ker g +rg\ g = \dim E = q$. Donc, $\dim\ker g = q-r$. Nous obtenons exactement ce que nous cherchions.

### 4.3 Mise en pratique

Conclusion de ce qui précède, nous savons déjà trouver  des équations cartésiennes d'un sev. Il suffit d'utiliser la fonction `noyau`.

La fonction `base_vers_eq` ci_dessous prend en paramètre une matrice $B$ de taille $q\times r$ censée représenter une base (une famille génératrice fonctionne aussi) d'un sous-espace vectoriel $F$ de $\mathbb R^q$ de dimension $r$. Elle renvoie les coefficients d'une famille d'équations cartésiennes de $F$.

__Remarque__ : Cette fonction __ne peut pas__ fonctionner si la matrice $B$ est vide, puisque dans ce cas on ne connaît pas la dimension de l'espace dans lequel on travaille. Voir une astuce dans les exemples qui suivent.

In [ ]:
def base_vers_eq(B):
    C = noyau(transp(B))
    return transp(C)

#### 4.3.1 Exemples basiques

Considérons la droite $D$ de $\mathbb R^3$ engendrée par le vecteur $(1,2,3)$.

In [ ]:
A = transp([[1, 2, 3]])
prnt(base_vers_eq(A))

Une famille d'équations de $D$ est donc

$$-2x+y=0$$
$$-3x+z=0$$

Reprenons notre exemple fétiche. 

In [ ]:
A = exemple(3, 3)
prnt(base_vers_eq(image(A)))

L'image de l'endomorphisme associé à $A$ est le plan d'équation $x-2y+z=0$.

In [ ]:
A = exemple(5, 7)
B = noyau(A)
prnt(B)
print()
eq = base_vers_eq(B) 
prnt(eq)

Cette fois-ci, le noyau de l'application linéaire de $\mathbb R^7$ vers $\mathbb R^5$ associée à $A$ est le sous-espace vectoriel de $\mathbb R^7$ de dimension 5 (deux équations !) d'équations

$$6x_1+5x_2+4x_3+3_4+2x_5+x_6=0$$
$$5x_1+4x_2+3x_3+2_4+x_5-x_7=0$$

Une vérification ? Facile ...

In [ ]:
prnt(prodmat(eq, B))

L'espace tout entier est décrit par la famille vide d'équations cartésiennes. Cela fonctionne-t-il ?

In [ ]:
E = eye(5)
base_vers_eq(E)

Oui, mais impossible à partir de cela de retrouver $E$ : nous avons perdu sa dimension.

À l'autre extrémité, quelles sont les équations de l'espace nul ? Une description de celui-ci par la base vide ne fonctionnera pas puisqu'on ne sait plus quelle est la dimension de l'espace entier. En revanche, en écrivant que le vecteur nul engendre l'espace nul, tout fonctionne.

In [ ]:
F = transp([[0, 0, 0, 0]])
prnt(base_vers_eq(F))

Le sev nul de $\mathbb R^4$ est donné par les équations $x=y=z=t=0$, ce qui, avouons-le, est logique.

#### 4.3.2 Un hyperplan de $\mathbb R^4$

Soit $H$ l'hyperplan de $\mathbb R^4$ engendré par les vecteurs $(1, 4, 2, 7)$, $(8, 6, 5, 13)$ et $(7,3,11, 1)$. Trouvons une équation cartésienne de $H$.

In [ ]:
U = [1, 4, 2, 7]
V = [8, 6, 5, 13]
W = [7, 3, 11, 1]
B = transp([U, V, W])
Phi = base_vers_eq(B)
prnt(Phi)

Vérifions :

In [ ]:
prnt(prodmat(Phi, B))

### 4.4 Équations cartésiennes vers bases

Soit $M\in\mathcal M_{(q-r)q}(\mathbb R)$ une matrice dont les lignes sont les coefficients des équations cartésiennes bans la base $\mathcal B$ d'un sev $F$ de l'espace vectoriel $E$. Soit $x\in E$. Soit $X$ la matrice de $x$ dans la base $\mathcal B$. Le vecteur $x$ est dans $F$ si et seulement si $MX=0$. En clair, trouver une base de $F$ c'est trouver une base du noyau d'une certaine application linéaire associée à $M$. En très clair, il n'y a quà utiliser la fonction `noyau`.

La fonction `eq_vers_base` prend en paramètre une matrice dont les ligne sont les coefficients des équations cartésiennes d'un sev $F$ de $E$. Elle renvoie une base de $F$. En fait, `eq_vers_base` = `noyau`.

__Remarque__ : Cette fonction __ne peut pas fonctionner__ lorsque la famille d'équations est vide, c'est à dire lorsque le sev cherché est l'espace entier.

In [ ]:
def eq_vers_base(E):
    return noyau(E)

Soit, par exemple, l'hyperplan de $\mathbb R^4$ d'équation $2x+3y+6z+t=0$.

In [ ]:
prnt(eq_vers_base([[2, 3, 6, 1]]))    

Une base de $F$ est $((-3,2,0,0), (-3,0,1,0), (-1,0,0,2))$.

In [ ]:
A = exemple(6, 8)
B = noyau(A)
prnt(B)

In [ ]:
E = base_vers_eq(B)
prnt(E)

In [ ]:
B1 = eq_vers_base(E)
prnt(B1)

## 5. Opérations sur les sous-espaces vectoriels

### 5.1 Introduction

Nous sommes maintenant capables de nous donner un sev $F$ d'un espace vectoriel $E$ :
- Au moyen d'une base de $F$.
- Au moyen d'une famille d'équations cartésiennes de $F$.

Dans ce qui suit nous allons voir qu'il est désormais facile de calculer des sommes, des intersections, de sev, ou de décider d'inclusions ou d'égalités de sev.

__Remarque__ : Nous supposerons que nos sev __sont donnés par une famille génératrice__. S'ils sont donnés par une famille d'équations cartésiennes, il suffit d'appeler `base` pour en obtenir une base. Si l'on en veut une base et pas seulement une famille génératrice il suffit d'appeler la fonction `image`.

### 5.2 Dimension

La dimension d'un sev est le nombre de vecteurs d'une base. Remarquer le traitement séparé de l'espace nul.

In [ ]:
def dimension(F):
    if F == []: return 0
    else:
        return nbcol(image(F))

### 5.3 Somme

Soient $F$, $G$ deux sev de $E$ donnés par une famille génératrice. Il suffit d'accoler les deux matrices représentant $F$ et $G$ "l'une à côté de l'autre" et d'appeler la fonction `image` pour obtenir une base de $F+G$. On examine à part le cas où l'un des sev est nul.

In [ ]:
def somme(F, G):
    if F == []: return G
    elif G == []: return F
    else:
        A = transp(transp(F) + transp(G))
        return image(A)

In [ ]:
F = transp([[1, 1, 2], [1, 0, 3]])
G = transp([[1, -1, 1], [1, 2, 3]])
prnt(somme(F, G))

### 5.4 Intersection

Soient $F$, $G$ deux sev de $E$ donnés par une famille génératrice. Pour obtenir une base de $F\cap G$, il suffit de

- Déterminer avec la fonction `eq_cart` des familles d'équations cartésiennes de $F$ et $G$.
- D'accoler ces matrices "l'une au-dessus de l'autre" : la matrice obtenue est la matrice d'une famille d'équations cartésiennes de $F\cap G$.
- D'appeler la fonction `base`.

On examine bien sûr à part le cas où l'un des deux espace est nul. Dans ce cas, l'intersection est l'espace nul. On renvoie la famille vide.

Il faut également régler le cas où $F=G=E$. Dans ce cas, la matrice $A$ ci-dessous est vide, on renvoie alors la matrice identité, base de $E$, dont on connaît la taille en regardant $F$ ou $G$.

In [ ]:
def intersect(F, G):
    if F == [] or G == []: return []
    else:
        A = base_vers_eq(F) + base_vers_eq(G)
        if A == []:
            if F != []: q = nblig(F)
            else: q = nblig(G)
            return eye(q)
        else:
            return eq_vers_base(A)

In [ ]:
F = transp([[1, 3, 3], [4, 5, 6]])
G = transp([[1, -1, 0],[1, 0, 2]])
prnt(intersect(F, G))

In [ ]:
F = []
G = transp([[1, -1, 0]])
prnt(intersect(F, G))

### 5.5 Inclusion, égalité

Soient $F$ et $G$ deux sev de $E$. Comment décider si $F\subset G$ ? C'est facile, puisque 

$$F\subset G \Longleftrightarrow \dim(F\cap G)=\dim F$$

In [ ]:
def inclus(F, G):
    return dimension(intersect(F, G)) == dimension(F)

In [ ]:
F = transp([[1, 1, 1]])
G = transp([[1, 2, 3], [4, 5, 6]])
inclus(F, G)

L'égalité de deux sev est alors immédiate.

In [ ]:
def egaux(F, G):
    return inclus(F, G) and dimension(F) == dimension(G)

In [ ]:
F = transp([[7, 8, 9], [10, 11, 12]])
G = transp([[1, 2, 3], [4, 5, 6]])
egaux(F, G)

Voici un dernier exemple où les deux espaces $F$ et $G$ sont égaux à $\mathbb R^5$, cas très particulier de la fonction `intersect`.

In [ ]:
F = exemple(5, 9)
G = exemple(5, 12)
egaux(F, G)

### 5.6 Somme directe, supplémentarité

Deux sev sont en somme directe si et seulement si leur intersection est $\{0\}$.

In [ ]:
def somme_directe(F, G):
    return dimension(intersect(F, G)) == 0

Deux sev sont supplémentaires si et seulement si
- Ils sont en somme directe, et
- La somme de leurs dimension est la dimension de l'espace.

Si $F$ et $G$ sont définis par la famille vide, il est impossible de trancher. En effet, si l'espace $E$ est l'espace nul alors ils sont supplémentaires. Sinon ils ne le sont pas. Mais on n'a aucun moyen de connaître la dimension de $E$ à partir des données !

Si, en revanche, l'un des deux sev est différent de $\{0\}$, la dimension de l'espace est le nombre de lignes de la matrice qui le définit.

In [ ]:
def dim_espace(F):
    if F == []: raise Exception('Indetermine')
    else: return nblig(F)

In [ ]:
def supplementaires(F, G):
    if F == [] and G == []: raise Exception('Indetermine')
    elif F == []: return dimension(G) == nblig(G)
    else:
        return somme_directe(F, G) and dimension(F) + dimension(G) == dim_espace(F)

In [ ]:
F = transp([[1, 2, 3]])
G = transp([[7, 5, 2], [6, 0, 4]])
supplementaires(F, G)

### 5.7 Bilan

L'espace nul et l'espace tout entier nous ont donné un peu de fil à retordre dans les dernières fonctions que nous avons écrites. Mais nous avons réussi à nous en sortir sauf dans un seul et unique cas. Nous ne saurons hélas jamais si $\{0\}\oplus \{0\}=E$ :-).